In [1]:
!pip install bs4
!pip install tqdm
!pip install elasticsearch
import datetime
import urllib.request
from bs4 import BeautifulSoup
import time
from elasticsearch import Elasticsearch, helpers

     |████████████████████████████████| 115 kB 543 kB/s eta 0:00:01
  Created wheel for bs4: filename=bs4-0.0.1-py3-none-any.whl size=2245 sha256=7862dfb9a6169042f2641da4da452395a8b1dfff3dc52e0b4ab7c9dc64af9e45
  Stored in directory: /root/.cache/pip/wheels/19/f5/6d/a97dd4f22376d4472d5f4c76c7646876052ff3166b3cf71050
Successfully built bs4
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.
     |████████████████████████████████| 69 kB 960 kB/s eta 0:00:011
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.
     |████████████████████████████████| 219 kB 586 kB/s eta 0:00:01
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [2]:
days_range = []

start = datetime.datetime.strptime("2020-09-01", "%Y-%m-%d")
end = datetime.datetime.strptime("2020-09-16", "%Y-%m-%d") # 범위 + 1
date_generated = [start + datetime.timedelta(days=x) for x in range(0, (end-start).days)]

for date in date_generated:
    days_range.append(date.strftime("%Y%m%d"))

print(days_range)

['20200901', '20200902', '20200903', '20200904', '20200905', '20200906', '20200907', '20200908', '20200909', '20200910', '20200911', '20200912', '20200913', '20200914', '20200915']


In [3]:
es = Elasticsearch("http://172.19.0.2:9200/")
es.info()

{'name': '6bc14c80abb0',
 'cluster_name': 'docker-cluster',
 'cluster_uuid': 'KRZ4avvNRqG8IDneQeJpAA',
 'version': {'number': '7.3.2',
  'build_flavor': 'default',
  'build_type': 'docker',
  'build_hash': '1c1faf1',
  'build_date': '2019-09-06T14:40:30.409026Z',
  'build_snapshot': False,
  'lucene_version': '8.1.0',
  'minimum_wire_compatibility_version': '6.8.0',
  'minimum_index_compatibility_version': '6.0.0-beta1'},
 'tagline': 'You Know, for Search'}

In [27]:
index_name = 'news'
es.indices.delete(index=index_name, ignore=[400, 404])
body = {
  "settings": {
    "analysis": {
      "analyzer": {
        "nori": {
          "tokenizer": "nori_tokenizer"
        }
      }
    }
  },
  "mappings": {
    "properties": {
      "title": {
        "type": "text",
        "fields": {
          "nori": {
            "type": "text",
            "analyzer": "nori"
          }
        }
      }
    }
  }
}

es.indices.create(index=index_name, body=body)

# doc = {'title': '한국어 처리 여야 하나?', 'url': 'naver.com'}
# es.index(index=index_name, doc_type='_doc', body=doc)

{'acknowledged': True, 'shards_acknowledged': True, 'index': 'news'}

In [29]:
# 기사 목록 가져오기
base_url = "https://news.naver.com/main/list.nhn?mode=LSD&mid=sec&date="
for date in days_range:
    date_url = base_url + (date)
    for i in range(400):
        url = date_url + "&sid1=" + str(i)
        response = urllib.request.urlopen(url)

        soup = BeautifulSoup(response, "html.parser")
        results = soup.select("dt.photo")

        for result in results:
            print("제목 : ", result.a.img.attrs["alt"])
            print("img_url : ", result.a.img.attrs["src"])
            print("url : ", result.a.attrs["href"])
            print("\n")
            doc = {
                'title': result.a.img.attrs["alt"],   
                'url': result.a.attrs["href"],
                'img' : result.a.img.attrs["src"]
            }
            es.index(index=index_name, doc_type='_doc', body=doc)

제목 :  BTS 30세까지 입영 연기 가능해지나…병역법 개정 추진
img_url :  https://imgnews.pstatic.net/image/origin/023/2020/09/01/3558500.jpg?type=ofullfill106_72
url :  https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=100&oid=023&aid=0003558500


제목 :  취임 100일 앞 김종인 페북 재개…"정부 왜 4차 추경 머뭇거리나"
img_url :  https://imgnews.pstatic.net/image/origin/003/2020/09/01/10053332.jpg?type=ofullfill106_72
url :  https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=100&oid=003&aid=0010053332


제목 :  [영상] '추미애 아들 질의' 불발...통합당 "전대미문 군기문란 사건"
img_url :  https://imgnews.pstatic.net/image/origin/421/2020/09/01/4847304.jpg?type=ofullfill106_72
url :  https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=100&oid=421&aid=0004847304


제목 :  "위헌 소지", "국회 경쟁력 떨어질 것" 통합당 '4연임 금지' 무산 운명이었나
img_url :  https://imgnews.pstatic.net/image/origin/277/2020/09/01/4747468.jpg?type=ofullfill106_72
url :  https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=100&oid=277&aid=0004747468


제목 :  김종인 “과감한 재정정책 기회지만…정부에 판단력 지닌 인

In [24]:
# test query
results = es.search(index=index_name, body={'from':0, 'size':10, 'query':{'match':{'title.nori':'자본'}}})
for result in results['hits']['hits']:
    print('score:', result['_score'], 'source:', result['_source'])

score: 9.943433 source: {'title': '<오후여담>노동자 vs 자본가', 'url': 'https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=281&oid=021&aid=0002441461'}
score: 8.872923 source: {'title': '티몬, PS얼라이언스서 4000억원 투자 유치…"자본잠식 해소"', 'url': 'https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=310&oid=421&aid=0004849504'}
score: 8.27873 source: {'title': '[김윤일의 역주행] ‘100패가 현실로?’야구 자본주의의 역설', 'url': 'https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=110&oid=119&aid=0002427498'}
score: 8.27873 source: {'title': '[김윤일의 역주행] ‘100패가 현실로?’야구 자본주의의 역설', 'url': 'https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=201&oid=119&aid=0002427498'}
score: 8.010511 source: {'title': '7월 유로존 산업생산 전월비 4.1% 상승..."자본재 등 확대"', 'url': 'https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=233&oid=003&aid=0010074948'}
score: 8.010511 source: {'title': '7월 유로존 산업생산 전월비 4.1% 상승..."자본재 등 확대"', 'url': 'https://news.naver.com/main/read.nhn?mode=LSD&mid=sec&sid1=262&oid=003&aid=0010074948'}
score: 